# *De Novo* Protein Design Workflow using NIMs

This example notebook outlines a workflow for creating *de novo* protein binders using NVIDIA Inference Microservices (NIMs). The process involves proposing protein backbones with RFDiffusion, generating sequences with ProteinMPNN, and predicting complex structures with AlphaFold-multimer. This workflow leverages advanced AI models to enable computational biologists to design novel protein structures efficiently.
The components include RFDiffusion for backbone design, ProteinMPNN for sequence optimization, and ESMFold for structure prediction. Users can substitute ESMFold with other models such as AlphaFold or AlphaFold-multimer as needed and here we will show how to chain these models together.
This setup provides a powerful framework for exploring protein design, offering flexibility and precision in generating functional protein binders. For more information, refer to the respective repositories and documentation.

## Workflow steps: 

1. **Visualize Initial Protein**: 3D visualization of the initial protein backbone, which helps in identifying regions for modification.
2. **Propose Region to Change**: Select specific areas of the backbone for redesign.
3. **Call RFDiffusion**: Use RFDiffusion to generate new protein backbones with desired features.
4. **Parse Result**: Ensure the generated backbones meet design specifications.
5. **Call ProteinMPNN**: Propose new amino acid sequences for the modified backbones, optimizing for stability and function.
6. **Parse Result**: Validate the proposed sequences.
7. **Call ESMFold**: Predict interactions of the designed protein sequences with a target by co-folding.
8. **Visualize Interaction**: Visualize the interaction between the designed protein and the target.

**Objectives**: 
modify a protein backbone, propose new sequences, use a folding model for the new sequences, use Alpha-fold2 multimere to assess target interaction quality. 

## Visualize initial protein

In [1]:
! pip install requests py3dmol Bio

Looking in indexes: https://pypi.org/simple, https://pypi.ngc.nvidia.com
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 281.0/281.0 kB 1.4 MB/s eta 0:00:00a 0:00:01m
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.2/3.2 MB 15.5 MB/s eta 0:00:00a 0:00:01

[notice] A new release of pip is available: 24.0 -> 24.3.1
[notice] To update, run: python -m pip install --upgrade pip


In [29]:
import json
import os
import requests
import py3Dmol
from pathlib import Path
import numpy as np
import matplotlib.pyplot as plt
import Bio
from Bio.PDB.PDBIO import PDBIO

# Download the protein
pdb_id = "1R42.pdb"
rcsb_path = os.path.join("https://files.rcsb.org/download", pdb_id)

def get_reduced_pdb(pdb_id=pdb_id, rcsb_path=rcsb_path):
    pdb = Path(pdb_id)
    if not pdb.exists():
        pdb.write_text(requests.get(rcsb_path).text)
    lines = filter(lambda line: line.startswith("ATOM"), pdb.read_text().split("\n"))
    return "\n".join(list(lines))#[:1000])

get_reduced_pdb()

# Visualize the predicted structure saved in PDB file
with open(pdb_id) as ifile:
    system = "".join([x for x in ifile])
#configuring the structure display
view = py3Dmol.view(width=600, height=400)
view.addModelsAsFrames(system)
view.setStyle({'model': -1}, {"cartoon": {'color': 'spectrum'}})
view.setStyle({'model': -1, 'chain': 'B'}, {"cartoon": {'hidden': True}})
view.setStyle({'model': -1, 'chain': 'C'}, {"cartoon": {'hidden': True}})
view.setStyle({'model': -1, 'chain': 'D'}, {"cartoon": {'hidden': True}})
view.setStyle({'model': -1, 'chain': 'E'}, {"cartoon": {'hidden': True}})
view.zoomTo()
view.show()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

### Getting started with NIMs

We rely on NIM instances hosted by NVIDIA for this tutorial. In order to run inferences, we need an API key.

Head to https://build.nvidia.com/ to get an API key and try the following out!


In [30]:
# Set the environment variable.
key = "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"

## RFDiffusion

This example demonstrates how to use RFDiffusion NIM in a *de novo* protein design workflow. Inspired by AI image generation models, RFDiffusion applies generative diffusion techniques to create novel protein structures. It excels in designing complex protein architectures, including binders and symmetric assemblies, by sculpting atomic clouds into functional proteins.

**Inputs**
- `input_pdb` is the protein target in PDB format
- `contigs` is the RFDiffusion language for how to specify regions to work on. See the official [RFDiffusion repo](https://github.com/RosettaCommons/RFdiffusion?tab=readme-ov-file#running-the-diffusion-script) for a full breakdown. A20-60/0 50-100 means to generate a binder to chain A residue 20-60, where the binder is 50-100 residues long. The /0 specifies a chain break.
- `hotspot_res` hot spot residues (specifically for binders)
- `diffusion_steps` number of diffusion_steps

**Output**:
- `output_pdb` is the output pdb
- `protein` is the input pdb


In [32]:
# RFDiffusion input language
reference_chain = 'A'
reference_residue_start = 20
reference_residue_end = 60
binder_length_min = 50
binder_length_max = 100
contigs = f"{reference_chain}{reference_residue_start}-{reference_residue_end}/0 {binder_length_min}-{binder_length_max}"
print(contigs)
hotspot_res = ["A50","A51","A52","A53","A54"]
steps = 15

# Pass the inference request with JSON payload to the NVIDIA server
rfdiffusion_r = requests.post(
    url=os.getenv("URL", "http://localhost:8002/biology/ipd/rfdiffusion/generate"),
    # headers={
    #     "Content-Type": "application/json",
    #     "Authorization": f"Bearer {key}"
    # },
    json={
        "input_pdb": get_reduced_pdb(),
        "contigs": contigs,
        "hotspot_res": hotspot_res,
        "diffusion_steps": steps,
    },
)

# Once we receive the result, save it
print(rfdiffusion_r, "Saving to output.pdb", rfdiffusion_r.text[:500])
binder_pdb_content = json.loads(rfdiffusion_r.text)["output_pdb"]
binder_pdb_fname = "RFDiffusion_output.pdb"
binder_pdb_path = Path(binder_pdb_fname)
binder_pdb_path.write_text(binder_pdb_content)


A20-60/0 50-100
<Response [200]> Saving to output.pdb {"output_pdb":"ATOM      1  N   GLY A   1     -10.688 -11.747  -6.431  1.00  0.00\nATOM      2  CA  GLY A   1      -9.699 -11.270  -5.472  1.00  0.00\nATOM      3  C   GLY A   1      -9.880  -9.784  -5.189  1.00  0.00\nATOM      4  O   GLY A   1     -10.281  -9.019  -6.066  1.00  0.00\nATOM      5  N   GLY A   2      -9.348  -9.355  -4.065  1.00  0.00\nATOM      6  CA  GLY A   2      -9.342  -7.926  -3.777  1.00  0.00\nATOM      7  C   GLY A   2      -8.260  -7.209  -4.575  1.00  0.00\nATOM     


36984

In [33]:
# Chain A is the designed backbone with GLY (placeholder residue names), and chain B is the input structure

print('\n'.join(binder_pdb_content.split('\n')[:10]))
print('\n'.join(binder_pdb_content.split('\n')[-10:]))


ATOM      1  N   GLY A   1     -10.688 -11.747  -6.431  1.00  0.00
ATOM      2  CA  GLY A   1      -9.699 -11.270  -5.472  1.00  0.00
ATOM      3  C   GLY A   1      -9.880  -9.784  -5.189  1.00  0.00
ATOM      4  O   GLY A   1     -10.281  -9.019  -6.066  1.00  0.00
ATOM      5  N   GLY A   2      -9.348  -9.355  -4.065  1.00  0.00
ATOM      6  CA  GLY A   2      -9.342  -7.926  -3.777  1.00  0.00
ATOM      7  C   GLY A   2      -8.260  -7.209  -4.575  1.00  0.00
ATOM      8  O   GLY A   2      -7.124  -7.675  -4.658  1.00  0.00
ATOM      9  N   GLY A   3      -8.614  -6.428  -5.508  1.00  0.00
ATOM     10  CA  GLY A   3      -7.643  -5.701  -6.316  1.00  0.00
ATOM    544  O   ASN B 136      -7.294   1.135 -13.530  1.00  1.00
ATOM    545  N   VAL B 137      -7.991   0.516 -15.510  1.00  1.00
ATOM    546  CA  VAL B 137      -7.695  -0.894 -15.292  1.00  1.00
ATOM    547  C   VAL B 137      -6.203  -1.171 -15.426  1.00  1.00
ATOM    548  O   VAL B 137      -5.644  -1.982 -14.688  1.00  

In [34]:
# Visualize the chains - notice that it is offset! Also notice it's a translational offset.

view = py3Dmol.view(width=600, height=400)
# Visualize the predicted structure saved in PDB file
with open(pdb_id) as ifile:
    system = "".join([x for x in ifile])
#configuring the structure display
view.addModelsAsFrames(system)
view.setStyle({'model': -1}, {"cartoon": {'color': 'blue'}})
view.setStyle({'model': -1, 'chain': 'B'}, {"cartoon": {'hidden': True}})
view.setStyle({'model': -1, 'chain': 'C'}, {"cartoon": {'hidden': True}})
view.setStyle({'model': -1, 'chain': 'D'}, {"cartoon": {'hidden': True}})
view.setStyle({'model': -1, 'chain': 'E'}, {"cartoon": {'hidden': True}})

with open('RFDiffusion_output.pdb') as ifile:
    system = "".join([x for x in ifile])
#configuring the structure display
view.addModelsAsFrames(system)
view.setStyle({'model': -1, 'chain': 'A'}, {"cartoon": {'color': 'red'}})
view.setStyle({'model': -1, 'chain': 'B'}, {"cartoon": {'color': 'green'}})

view.zoomTo()
view.show()


3Dmol.js failed to load for some reason. Please check your browser console for error messages.

In [35]:
# Use Bio.PDB to align the two structures - chain A from 1R42.pdb and chain B from output.pdb.
# Since we only need a translational alignment, just find the same atom in each file and translate output.pdb.

parser = Bio.PDB.PDBParser(QUIET=True)
ref_structure = parser.get_structure('1R42', '1R42.pdb')
binder_structure = parser.get_structure('binder', binder_pdb_fname)

# CA atom of first residue in chain B from the RFDiffusion output file (output.pdb)
# is the CA atom of the first residue in the contig specification of 1R42.pdb
binder_point = list(binder_structure[0]['B'])[0]['CA'].get_coord()
ref_point = ref_structure[0]['A'][reference_residue_start]['CA'].get_coord()
transformation = ref_point - binder_point
binder_structure.transform(np.eye(3), transformation)

In [36]:
# Save the aligned output for visualization

io = PDBIO()
io.set_structure(binder_structure)
aligned_binder_pdb_fname = 'RFDiffusion_output_aligned.pdb'
aligned_binder_pdb_path = Path(aligned_binder_pdb_fname)
io.save(aligned_binder_pdb_fname)


In [37]:
# Visualize the chains again - Now they are aligned!

view = py3Dmol.view(width=600, height=400)
# Visualize the predicted structure saved in PDB file
with open(pdb_id) as ifile:
    system = "".join([x for x in ifile])
# configuring the structure display
view.addModelsAsFrames(system)
view.setStyle({'model': -1}, {"cartoon": {'color': 'blue'}})
view.setStyle({'model': -1, 'chain': 'B'}, {"cartoon": {'hidden': True}})
view.setStyle({'model': -1, 'chain': 'C'}, {"cartoon": {'hidden': True}})
view.setStyle({'model': -1, 'chain': 'D'}, {"cartoon": {'hidden': True}})
view.setStyle({'model': -1, 'chain': 'E'}, {"cartoon": {'hidden': True}})

with open(aligned_binder_pdb_fname) as ifile:
    system = "".join([x for x in ifile])
#configuring the structure display
view.addModelsAsFrames(system)
# Designed structure
view.setStyle({'model': -1, 'chain': 'A'}, {"cartoon": {'color': 'red'}}) 
# Reference that's input to RFDiffusion
view.setStyle({'model': -1, 'chain': 'B'}, {"cartoon": {'color': 'green'}}) 

view.zoomTo()
view.show()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

## ProteinMPNN
ProteinMPNN (Protein Message Passing Neural Network) is a deep learning-based graph neural network used in *de novo* protein design workflows. It predicts amino acid sequences for given protein backbones, leveraging evolutionary, functional, and structural information to generate sequences that are likely to fold into the desired 3D structures. This tool integrates seamlessly with NIMs into workflows involving RFDiffusion for backbone generation and AlphaFold-2 Multimer for interaction prediction, enhancing the accuracy and efficiency of protein design.

**Inputs**: 
- `input_pdb` Input protein for which amino acid sequences need to be predicted
- `ca_only` Defaults to false, CA-only model helps to address specific needs in protein design where focusing on the alpha carbon (CA)
- `use_soluble_model` ProteinMPNN offers soluble models for applications requiring high solubility and non-soluble models for membrane protein studies and industrial applications where solubility is less critical.
- `num_seq_per_target` how many seqs to generate for a given target protein structure
- `sampling_temp` ranges from 0 to 1 ranges from 0 to 1 and controls the diversity of design outcomes by adjusting the probability values for the 20 amino acids at each sequence position. Higher values increase
 
**Outputs**:
- `ProteinMPNN.fa` which is a fasta file containing the generated sequences for the given structure.


In [38]:
# ProteinMPNN parameters
ca_only = False
use_soluble_model = False
sampling_temp = [0.5]
num_seq_per_target = 20

# Read the content of the binder PDB file
if aligned_binder_pdb_path.exists():
    input_pdb_content = aligned_binder_pdb_path.read_text()
else:
    raise FileNotFoundError(f"{aligned_binder_pdb_path} does not exist")

# You know the drill - pass JSON payload to the inference server
proteinMPNN_r = requests.post(
    url=os.getenv("URL", "http://localhost:8003/biology/ipd/proteinmpnn/predict"),
    # headers={
    #     "Content-Type": "application/json",
    #     "Authorization": f"Bearer {key}"
    # },
    json={
        "input_pdb": input_pdb_content,
        "input_pdb_chains": ['A'],
        "ca_only": ca_only,
        "use_soluble_model": use_soluble_model,
        "num_seq_per_target": num_seq_per_target,
        "sampling_temp": sampling_temp,
    },
)

print(proteinMPNN_r, "Saving to output.fa:\n", proteinMPNN_r.text[:200], "...")

# Assign the content to a variable
output_fa_content = json.loads(proteinMPNN_r.text)["mfasta"]
output_fa_path = Path("ProteinMPNN_output.fa")
output_fa_path.write_text(output_fa_content)

# Now you can access the content using the variable `output_fa_content` or the path `output_fa_path`

<Response [200]> Saving to output.fa:
 {"mfasta":">input, score=2.4192, global_score=2.4743, fixed_chains=['B'], designed_chains=['A'], model_name=v_48_002, git_hash=unknown, seed=953\nGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGG ...


3663

In [39]:
# List the resulting sequences - first one is the reference, the rest are designed sequences
output_fa_content.split('\n')[1::2]

['GGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGGG',
 'MNTGTTCYLVYKGCKGECAKAKCLSSTKDDKTCNSKTRNLGNEYRACLTGAENIEGKAEGPRILKNSPISVKCDICSDKKSLGGIIPVEVVTREEAQ',
 'HCHECICDLINKGCNGKCKEAECLSSCEDAETCCSLLCIDDDEKKRCETGAENVDGEATGPKTSKESPIFVQCEKNVSVNKLGGIAPVEVITKEEAL',
 'MNSEDTAYLKTKGCTGDCAKAQALGSDTKKETCSSKEGVEENEYKRCQTGARNVGGEAIGKDTDFVKAVFVKCPTCNDMDHLGGIIPVDVVTGEEAQ',
 'MNSATIAALVRKGCRGECAKAKALGSDEDINSCSSKVNEYKNEYKRDHTGAENKRGVAEGPETGLLPPIFLNCNVCTSEEKLGGIIPVDVVKKDDAN',
 'MRIDALCSLVFNGCKGECQKAKCLGSDRNRKTCNSDTGDEQNEWLRCLTGAENVDGKAQGPNQAKIPAISSKCPNCTEVSKLGGIIDVSVVKEEEAK',
 'SNEGCLAYLRKKGCSGKCAKAESLGSDENVETCNSLRGVGENERRRCETGAENVGGKAEGPRKEELQPLTVKCENCTSIQHLGDIIPVDVVTREQAL',
 'HCEECTCYLVFRGCTGKCSKAECIGSCFNSQTCSSLSGIEEDEYKRCQTGAERVEGKSVGPAKLKEKPIFVKCPTCVDAEHLGGILDLEVVSEEQAR',
 'DCEECLCSLVRQGCDGECAKAECRSSCSNKSSCCSSRNVSDNEYTRCYTGRENRNGFAEGPRTDRQKSICHQCRRCTSKAKLGGIIDVEVVTDAQAR',
 'RNRNSLCSLVHKGCAGKCKEAKCYSSCKDEKTCCSKKNVSENEYKRCLTGAQNVNGNAVGPKVQKNSPICHKCENCQSIS

## Validate designs

After designing the sequences with ProteinMPNN, we can use a range of methods to validate the sequences:
1. Use ESMFold to predict structures of the designed sequences, and judge by their pLDDT scores. pLDDT is a metric of the model's confidence of prediction. Additionally, we judge by how similar they fold to the structure that RFDiffusion designed.
2. Similarly, do it with AlphaFold2 but without MSA, and judge by pLDDT scores.
3. Use AlphaFold-Multimer to model the complex

In this notebook we will show only the first method, as it is the fastest.

## ESMFold
ESMFold is a protein structure prediction deep learning model developed by Facebook AI Research (FAIR). The model was inspired by AlphaFold, but does not require multiple sequence alignment (MSA) as an input, leading to significantly faster inference times for protein structure prediction that is nearly as accurate as alignment-based methods.

**Inputs**: 
- `seq`: The protein sequence
 
**Outputs**:
- `ESMFold_results/seq<N>.pdb` which is a fasta file containing the generated sequences for the given structure.

In [40]:
# Read the content of the sequence design file
if output_fa_path.exists():
    input_fa_content = output_fa_path.read_text()
else:
    raise FileNotFoundError(f"{output_fa_path} does not exist")

# Condense sequences by text processing, removing the first entry as it is input
seqs = [x for x in input_fa_content.strip().split('\n') if '>' not in x][1:]

ESM_results = []
os.makedirs('ESMFold_results/', exist_ok=True)

for idx, seq in enumerate(seqs): 
    ESMFold_r = requests.post(
        url=os.getenv("URL", "https://health.api.nvidia.com/v1/biology/nvidia/esmfold"),
        headers={
            "Content-Type": "application/json",
            "Authorization": f"Bearer {key}"
        },
        json={
            "sequence": seq
        },
    )
    ESM_result = json.loads(ESMFold_r.text)["pdbs"][0]
    ESM_results.append(ESM_result)
    output_ESMFold_path = Path(f"ESMFold_results/seq{idx}.pdb")
    output_ESMFold_path.write_text(ESM_result)
    print(ESMFold_r, "Saving to pdb:\n", ESMFold_r.text[:200], "...")



<Response [200]> Saving to pdb:
 {"pdbs":["PARENT N/A                                                                      \nMODEL     1                                                                     \nATOM      1  N   MET A   1 ...
<Response [200]> Saving to pdb:
 {"pdbs":["PARENT N/A                                                                      \nMODEL     1                                                                     \nATOM      1  N   HIS A   1 ...
<Response [200]> Saving to pdb:
 {"pdbs":["PARENT N/A                                                                      \nMODEL     1                                                                     \nATOM      1  N   MET A   1 ...
<Response [200]> Saving to pdb:
 {"pdbs":["PARENT N/A                                                                      \nMODEL     1                                                                     \nATOM      1  N   MET A   1 ...
<Response [200]> Saving to pdb:
 {"pdbs":["PAREN

In [41]:
# Function to calculate average pLDDT over all residues of a PDB file
def calculate_average_pLDDT(pdb_string):
    # Someone really smart wrote this
    total_pLDDT = 0.0
    atom_count = 0
    pLDDTs = []
    pdb_lines = pdb_string.splitlines()
    for line in pdb_lines:
        # PDB atom records start with "ATOM"
        if line.startswith("ATOM"):
            atom_name = line[12:16].strip()  # Extract atom name (columns 13-16)
            if atom_name == "N":  # Only consider atoms with name "N"
                try:
                    # Extract the B-factor value from columns 61-66 (following PDB format specifications)
                    pLDDT = float(line[60:66].strip())
                    pLDDTs.append(pLDDT)
                    total_pLDDT += pLDDT
                    atom_count += 1
                except ValueError:
                    pass  # Skip lines where B-factor can't be parsed as a float

    if atom_count == 0:
        return 0.0  # Return 0 if no N atoms were found

    average_pLDDT = total_pLDDT / atom_count
    return average_pLDDT


# List the average b factors of these outputs
pLDDTs = np.array([calculate_average_pLDDT(ESM_results[x]) for x in range(num_seq_per_target)])
print(pLDDTs)

[33.10185567 37.5685567  36.60226804 39.39195876 33.12649485 40.01134021
 32.76185567 34.27175258 32.34185567 34.2671134  35.28391753 27.79659794
 32.52886598 32.38329897 30.64092784 33.71525773 32.76206186 33.86752577
 31.8556701  33.2443299 ]


In [42]:
def calc_RMSD(coord1, coord2):
    # coord is a N*3 matrix. Must have same shape
    return np.sqrt(((coord2-coord1)**2).sum(1)).sum() / len(coord1)

In [43]:
# Calculate RMSD of RFDiffusion-designed backbone and folded structure

# RFDiffusion structure
binder_CA = [x['CA'] for x in list(binder_structure[0]['A'])]
binder_CA_coord = np.array([x.get_coord() for x in binder_CA])

# Align all output seqs to the output_aligned A chain, and calculate RMSD
RMSDs = []
si = Bio.PDB.Superimposer()
os.makedirs('ESMFold_results_aligned', exist_ok=True)
for i in range(num_seq_per_target):
    pid = f'seq{i}'
    unaligned_ESMFold = parser.get_structure(pid, f'ESMFold_results/{pid}.pdb')
    folded_CA = [x['CA'] for x in list(unaligned_ESMFold[0]['A'])]
    si.set_atoms(binder_CA, folded_CA)
    si.apply(unaligned_ESMFold)
    folded_CA_coord = np.array([x.get_coord() for x in folded_CA])
    RMSDs.append(calc_RMSD(folded_CA_coord, binder_CA_coord))
    io.set_structure(unaligned_ESMFold)
    io.save(f'ESMFold_results_aligned/{pid}.pdb')
RMSDs = np.array(RMSDs)


In [18]:
# List RMSD and pLDDTs of the sequences
list(zip(RMSDs, pLDDTs))

[(13.103426597559501, 44.1496),
 (13.682475770808741, 45.517799999999994),
 (10.730880216135114, 43.241400000000006),
 (15.765870227898308, 43.1758),
 (10.93853065591803, 52.44500000000001),
 (15.910180191940297, 49.102199999999996),
 (10.158197183849353, 52.44879999999999),
 (8.195272145932615, 45.609399999999994),
 (7.860027535727488, 49.39279999999999),
 (11.096182618415622, 41.7664),
 (10.49110420579019, 45.709399999999995),
 (8.649855701952616, 42.456),
 (16.22819876741906, 51.93599999999999),
 (12.224194750007843, 42.791),
 (11.521690372702176, 39.70819999999999),
 (14.406672402616994, 40.2566),
 (12.404087146716995, 54.2808),
 (15.211115196909718, 51.003),
 (11.977124461674721, 46.061400000000006),
 (14.95758499406616, 44.80219999999999)]

In [44]:
# Perform filtering - you're free to change the criteria
qualified_list = (pLDDTs > 85)
print(f'There are {np.sum(qualified_list)} sequences that passed test')
ranking = RMSDs
ranking[~qualified_list] = np.inf

There are 0 sequences that passed test


In [20]:
# Select a qualified sequence that's closest to the RFDiffusion structure
best_RMSD_index = np.argmin(ranking)

print(f'The best sequence is number {best_RMSD_index}, with an RMSD of {RMSDs[best_RMSD_index]:.2f} and a pLDDT of {pLDDTs[best_RMSD_index]:.2f}')


The best sequence is number 0, with an RMSD of inf and a pLDDT of 44.15


In [21]:
# Visualize the predicted structure saved in PDB file
view = py3Dmol.view(width=750, height=600)

with open(pdb_id) as ifile:
    system = "".join([x for x in ifile])
#configuring the structure display
view.addModelsAsFrames(system)
view.setStyle({'model': -1}, {"cartoon": {'color': 'orange'}})

with open(aligned_binder_pdb_fname) as ifile:
    system = "".join([x for x in ifile])
#configuring the structure display
view.addModelsAsFrames(system)
view.setStyle({'model': -1, 'chain': 'A'}, {"cartoon": {'color': 'green'}})
view.setStyle({'model': -1, 'chain': 'B'}, {"cartoon": {'hidden': True, 'color': 'green'}})


# for i in [best_pLDDT]:

with open(f'ESMFold_results_aligned/seq{best_RMSD_index}.pdb', 'r') as f:
    system = f.read()
    view.addModelsAsFrames(system)
    pLDDT = calculate_average_pLDDT(system)
    print(f'Seq {i}: RMSD {RMSDs[best_RMSD_index]:.2f} A, pLDDT {pLDDT:.2f}')
    view.setStyle({'model': -1}, {"cartoon": {'color': 'cyan'}, "stick": {}})
            
#configuring the structure display

view.zoomTo()
view.show()

Seq 19: RMSD inf A, pLDDT 44.15


3Dmol.js failed to load for some reason. Please check your browser console for error messages.

## **Voila! There you have it. A designed binder in a few minutes.**

### Next steps on the workflow

1. Learn how to instead use AlphaFold to perform folding
2. Use AlphaFold-multimer to directly model the complex

### Next steps on the engineering

1. Learn how to host all three models as NIMs on your local machine
2. Easily adapt this notebook to call your local NIMs and get the same result.